In [1]:
# generate data for testing acc@10
# pair all proteins with all ligands
# (total of 800,000 pairs...)

In [2]:
from pathlib import Path
import numpy as np
import pickle as pk
from multiprocessing import Pool
import pandas as pd
from tqdm import tqdm
from htmd.ui import *
from htmd.molecule.voxeldescriptors import *
from multiprocessing import Pool 
from pdb_parser import test_pdb_to_features

%load_ext autoreload
%autoreload 2
%cd ..

#Supress default INFO logging
import logging
logger = logging.getLogger()
logger.setLevel(logging.CRITICAL)

ffevaluate module is in beta version

Please cite HTMD: Doerr et al.(2016)JCTC,12,1845. 
https://dx.doi.org/10.1021/acs.jctc.6b00049
Documentation: http://software.acellera.com/
To update: conda update htmd -c acellera -c psi4



2018-10-28 19:11:55,296 - binstar - INFO - Using Anaconda API: https://api.anaconda.org


You are on the latest HTMD version (1.13.9).



/home/alex/miniconda3/lib/python3.6/site-packages/pyemma/__init__.py:91: UserWarning: You are not using the latest release of PyEMMA. Latest is 2.5.2, you have 2.4.
  .format(latest=latest, current=current), category=UserWarning)


/home/alex/Desktop/tmp/drug-discovery


In [3]:
base_dest = './processed_data/eval/test_acc10'
Path(base_dest).mkdir(exist_ok=True, parents=True)
df = pd.read_csv('./data/csv/ligand_data_eval.csv')
idxs = sorted(list(df.id.unique()))

In [ ]:

# generate the data & csv
dests = []
ligs = []
proteins = []
score = []

for lig_idx in tqdm(idxs):
    lig_src = './processed_data/eval/ligands/' + str(lig_idx).zfill(4) + '.pk'
    with open(lig_src, 'rb') as f:
        lig_features, centers = pk.load(f)
    
    for pro_idx in idxs:
        dest = base_dest + '/' + str(pro_idx).zfill(4) + '_pro_' + str(lig_idx).zfill(4) + '_lig.npy'
        if not Path(dest).exists():
            protein_path = './data/testing_data/'+str(pro_idx).zfill(4)+'_pro_cg.pdb'

            pro_features, _ = test_pdb_to_features(protein_path, centers)
            pro_features = pro_features[:,:,:,0]
            combined = np.concatenate((pro_features[:,:,:,None], lig_features[:,:,:,None]), axis=3)
            combined = combined.astype(np.float32)

            np.save(dest, combined)
        else:
            pass
            #print(f'Skipping {dest}')
        
        dests.append(dest)
        ligs.append(lig_idx)
        proteins.append(pro_idx)






  0%|          | 0/824 [00:00<?, ?it/s]




  1%|          | 9/824 [00:00<00:09, 89.01it/s]




  2%|▏         | 19/824 [00:00<00:09, 89.39it/s]




  3%|▎         | 27/824 [00:00<00:09, 86.04it/s]




  4%|▍         | 36/824 [00:00<00:09, 86.15it/s]




  5%|▌         | 45/824 [00:00<00:09, 86.06it/s]




  7%|▋         | 54/824 [00:00<00:08, 86.21it/s]




  8%|▊         | 63/824 [00:00<00:08, 85.15it/s]




  9%|▊         | 72/824 [00:00<00:08, 85.74it/s]




 10%|▉         | 81/824 [00:00<00:08, 83.19it/s]




 11%|█         | 90/824 [00:01<00:08, 83.18it/s]




 12%|█▏        | 99/824 [00:01<00:08, 84.53it/s]




 13%|█▎        | 108/824 [00:01<00:08, 84.61it/s]




 14%|█▍        | 117/824 [00:01<00:08, 80.49it/s]




 15%|█▌        | 126/824 [00:01<00:08, 79.52it/s]




 16%|█▋        | 134/824 [00:01<00:08, 77.85it/s]




 17%|█▋        | 143/824 [00:01<00:08, 79.75it/s]




 18%|█▊        | 152/824 [00:01<00:08, 82.02it/s]




 20%|█▉        | 161/824 [00:01<00:07, 83.36i

In [ ]:
csv_dest = f'./data/csv/test_acc10_{test_size}.csv'
pro_lig_record = pd.DataFrame({'lig_id': ligs, 'pro_id': proteins, 
                               'dest': dests,}, index=None)
pro_lig_record.to_csv(csv_dest, index=None)